In [1]:
import folium
m = folium.Map(location=[39.7392, -104.9903])

In [2]:
m

In [5]:
m.save('test_folium.html')

In [9]:
m = folium.Map(location=[48, -102], zoom_start=3)
m

In [13]:
import branca
import pandas as pd
import json
import requests

url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
county_data = f'{url}/us_county_data.csv'
county_geo = f'{url}/us_counties_20m_topo.json'


df = pd.read_csv(county_data, na_values=[' '])

colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 50e3)
employed_series = df.set_index('FIPS_Code')['Employed_2011']


def style_function(feature):
    employed = employed_series.get(int(feature['id'][-5:]), None)
    return {
        'fillOpacity': 0.5,
        'weight': 0,
        'fillColor': '#black' if employed is None else colorscale(employed)
    }


m = folium.Map(
    location=[48, -102],
    tiles='cartodbpositron',
    zoom_start=3
)

folium.TopoJson(
    json.loads(requests.get(county_geo).text),
    'objects.us_counties_20m',
    style_function=style_function
).add_to(m)


m

In [71]:
import branca
import pandas as pd
import json
import requests

block_group_geo = '../data/denver.json'

df = pd.read_pickle('../data/pickled_df_2014_2018')

# colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 50e3)
data_series = df.set_index('STFID')['MED_HH_INCOME']

# def style_function(feature):
#     employed = data_series.get(int(feature['id'][-5:]), None)
#     return {
#         'fillOpacity': 0.5,
#         'weight': 0,
#         'fillColor': '#black' if employed is None else colorscale(employed)
#     }


m = folium.Map(
    location=[39.7392, -104.9903],
    zoom_start=12
)

# folium.TopoJson(
#     json.loads(open(block_group_geo, 'r').read()),
#     'objects.us_counties_20m',
#     style_function=style_function
# ).add_to(m)

folium.Choropleth(
    geo_data=block_group_geo,
    name='choropleth',
    data=df,
    columns=['STFID', 'MED_HH_INCOME'],
    key_on='feature.id',
    fill_color='YlGn',
    fill_opacity=0.3,
    line_opacity=0.2,
    legend_name='Median Income ($)'
).add_to(m)

folium.LayerControl().add_to(m)

m